# D3.js 應用

## 目次
- [使用地圖資料](#使用地圖資料)
- [使用 Leaflet 建立地圖](#使用-Leaflet-建立地圖)
- [製作 Force-Directed Graph](#製作-Force-Directed-Graph)

## 使用地圖資料

### 地圖資料格式

要在 D3.js 中使用地圖資料，需要使用 GeoJSON 格式，GeoJSON 主要是基於 JSON 編寫的一種地理交換資料格式，其格式如下：

```JSON
{
	"type" : "FeatureCollection",
	"features" : [
		{
		  "type": "Feature",
		  "geometry": {
		    "type": "Point",
		    "coordinates": [51.507351, -0.127758]
		  },
		  "properties": {
		    "name": "London"
		  }
		},
		{
			...
		}
	]
}
```

#### TopoJSON

為 GeoJSON 的改良版格式，將 GeoJSON 中的重複邊或點做簡化處理，能夠大幅減少使用空間，  
但是 TopoJSON 不能直接為 D3.js 所接受，必須經過轉換才能使用，轉換可使用 Topojson 函式庫

In [ ]:
%%html
<script src="https://unpkg.com/topojson@3"></script>

引入 D3.js

In [ ]:
%%html
<script src="https://d3js.org/d3.v6.min.js"></script>

### 取得地圖資料

參考以下網址可以取得臺灣的地圖資料  
[繪製臺灣地圖(ithelp.ithome.com.tw)](https://ithelp.ithome.com.tw/articles/10223786)

這裡使用已經轉換成 TopoJSON 的地圖資料  
[https://raw.githubusercontent.com/Zovjsra/taiwan-map/main/COUNTY_MOI_1090820.json](https://raw.githubusercontent.com/Zovjsra/taiwan-map/main/COUNTY_MOI_1090820.json)

使用 `d3.json()` 讀取檔案

In [ ]:
let svg = d3.select('#canvas').append('svg').style('height', 500).style('width', 500)

let tooltip = d3.select('#tooltip').style('position', 'absolute')
    .style('background', 'blue')
    .style('width', 100)
    .style('height', 50)
    .style('display', 'none')

d3.select('#canvas').on('mousemove', function(e){
    tooltip.style('left', e.layerX + 20).style('top', e.layerY + 35)
})

d3.json('https://raw.githubusercontent.com/Zovjsra/taiwan-map/main/COUNTY_MOI_1090820.json').then((data) => {
    const counties = topojson.feature(data, data.objects.COUNTY_MOI_1090820)
	const projection = d3.geoMercator().center([123, 24]).scale(5000);
    const projection2 = d3.geoMercator().center([123, 24]).scale(10000);
	const path = d3.geoPath().projection;
	
	const geoPath = svg.selectAll('.geo-path')
        .data(counties.features)
        .join('path')
        .attr('class', 'geo-path')
        .attr('d', path(projection))
        .style('fill', 'green')
        .on('mouseover', function(e){
            d3.select(this).style('stroke', 'white')
            d3.select(this).select(function(d){
                tooltip.select('text').html(d.properties.COUNTYNAME)
                tooltip.style('display', 'block')
            })
        })
        .on('mouseleave', function(e){
            d3.select(this).style('stroke', 'none')
            tooltip.style('display', 'none')
        })
    
    const texts = svg.selectAll('text')
        .data(counties.features)
        .enter()
        .append('text')
        .attr('x', (d, i) => {
            return path(projection).centroid(d)[0]
        })
        .attr('y', (d, i) => {
            return path(projection).centroid(d)[1]
        }).attr('text-anchor', 'middle')
        .attr('font-size', '8px')
        .text((d, i) =>{
            return d.properties.COUNTYNAME
        })
})

[完整程式碼](https://codepen.io/zovjsra/pen/KKaLapE)

### 程式說明

#### html
這個範例的 html 主要是一個 canvas，裡面有一個 svg，但是這個 svg 是作為 tooltip 使用的，  
畫布的 svg 會由 D3.js 來增加

Tooltip 的 svg 中，有一個 text，是用來顯示縣市名稱的，後面會由程式修改裡面的文字。

```html
<div id='canvas'>
    <svg id='tooltip'>
        <text x='50%' y='50%' style='text-anchor: middle; fill: white'>hello</text>
    </svg>
</div>
```

#### JavaScript

首先我們要在 canvas 中加入 svg
```js
let svg = d3.select('#canvas').append('svg').style('height', 500).style('width', 500)
```

設定 tooltip 的性質  

`.style('position', 'absolute')` 使得 tooltip 的位置不影響網頁的其他元素
`.style('display', 'none')` 使得 tooltip 預設為不顯示

```js
let tooltip = d3.select('#tooltip').style('position', 'absolute')
    .style('background', 'blue')
    .style('width', 100)
    .style('height', 50)
    .style('display', 'none')
```

接著使 tooltip 的位置跟隨滑鼠，其中 `e.layerX`，`e.layerY` 代表滑鼠在 div 中的相對位置
```js
d3.select('#canvas').on('mousemove', function(e){
    tooltip.style('left', e.layerX + 20).style('top', e.layerY + 35)
})
```

用 `d3.json()` 讀取外部地圖檔案
```js
d3.json('https://raw.githubusercontent.com/Zovjsra/taiwan-map/main/COUNTY_MOI_1090820.json').then((data) => {
    ...    
})
```

使用 topojson 將 TopoJSON 格式轉換為 GeoJSON 格式
```js
const counties = topojson.feature(data, data.objects.COUNTY_MOI_1090820)
```

設定地圖的投影法，這裡使用常用的麥卡托投影法，並使用 `.center([X, Y])` 來指定中心的經緯度，`.scale()` 指定縮放的大小  
[D3.geo(github)](https://github.com/d3/d3-geo)
```js
const projection = d3.geoMercator().center([123, 24]).scale(5000);
```

生成 geoPath 物件，內容是地圖的外框座標
```js
const path = d3.geoPath().projection(projection);
```

用 geoPath 物件在 svg 上畫上地圖，並使用剛才轉換的 counties 作為資料
```js
const geoPath = svg.selectAll('.geo-path')
    .data(counties.features)
    .join('path')
    .attr('class', 'geo-path')
```

使用 path 設定外框的座標
```js
    .attr('d', path)
    .style('fill', 'green')
```

設定滑鼠進入的動作
```js
    .on('mouseover', function(e){
        d3.select(this).style('stroke', 'white')
        d3.select(this).select(function(d){
            tooltip.select('text').html(d.properties.COUNTYNAME)
            tooltip.style('display', 'block')     //顯示 tooltip
        })
    })
```
設定滑鼠離開的動作
```js
    .on('mouseleave', function(e){
        d3.select(this).style('stroke', 'none')
        tooltip.style('display', 'none')          //隱藏 tooltip
    })
```

## 使用 Leaflet 建立地圖

[QuickStart(leafletjs.com)](https://leafletjs.com/examples/quick-start/)

Leaflet 提供了方便的函式庫，讓我們可以快速地建立一個地圖並在地圖上添加內容

首先必須載入 Leaflet 的 CSS 以及 JS（順序不能顛倒）

In [ ]:
%%html

<!--載入leaflet的CSS-->
<link rel="stylesheet" href="https://unpkg.com/leaflet@1.7.1/dist/leaflet.css"
   integrity="sha512-xodZBNTC5n17Xt2atTPuE1HxjVMSvLVW9ocqUKLsCC5CXdbqCmblAshOMAS6/keqq/sMZMZ19scR4PsZChSR7A=="
   crossorigin=""/>

<!--載入leaflet的JS-->
<script src="https://unpkg.com/leaflet@1.7.1/dist/leaflet.js"
   integrity="sha512-XQoYMqMTK8LvdxXYG3nZ448hOEQiglfqkJs1NOQV44cWnUrBc8PkAOcXy20w0vlaXaVUearIOBhiXZ5V3ynxwA=="
   crossorigin=""></script>

接著定義畫布

In [ ]:
%%html

<div id="mapid" style="width: 600px; height: 400px;"></div>

接著就可以用 `L.map(id).setView(經緯度, 縮放)` 設定地圖的初始位置

In [ ]:
%%html

<script>
var mymap = L.map('mapid').setView([24.986909, 121.576520], 16)
</script>

接著需要載入地圖資料，這裡的 accessToken 需要到 [www.mapbox.com](https://www.mapbox.com/studio/account/tokens/) 申請帳號取得。  
如果有自己常用的地圖來源，也可以使用其他的來源

In [ ]:
%%html

<script>
L.tileLayer('https://api.mapbox.com/styles/v1/{id}/tiles/{z}/{x}/{y}?access_token={accessToken}', {
    attribution: 'Map data &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors, Imagery © <a href="https://www.mapbox.com/">Mapbox</a>',
    maxZoom: 18,
    id: 'mapbox/streets-v11',
    tileSize: 512,
    zoomOffset: -1,
    accessToken: 'pk.eyJ1Ijoiem92anNyYSIsImEiOiJja283MzYwdTgxNGV6Mm9zN2Nnd3U1NjRzIn0.c2pLwdmzD19cTv4nm9ocTw'
}).addTo(mymap);
</script>

接著我們就可以在地圖上面加入圖釘、圓圈等標記

### 加入圖釘

使用 `L.marker(經緯度).addTo(mymap)` 可以加入圖釘

In [ ]:
%%html

<script>
let marker = L.marker([24.987393, 121.576845]).addTo(mymap)
</script>

### 加入圓圈
使用 `L.circle(經緯度, 屬性)` 可以加入圓圈

In [ ]:
%%html

<script>
let circle = L.circle([24.987152, 121.573554], {
    color: 'red',
    fillColor: '#f03',
    fillOpacity: 0.5,
    radius: 50
}).addTo(mymap);
</script>

### 加入 Popup

使用 `marker.bindPopup(html內容)` 可以加入 Popup

再加入 `.openPopup()` 可以使 popup 預設為打開的狀態

In [ ]:
%%html

<script>
circle.bindPopup("大仁樓").openPopup()
</script>

[完整程式碼](https://codepen.io/zovjsra/pen/abpezPE)

## 製作 Force-Directed Graph

[Force-Directed Graph(bl.ocks.org)](https://bl.ocks.org/mbostock/4062045)

Force-Directed Graph 是一種由 node 和 link 組成的圖形，其中 link 的長度愈大代表兩個 node 之間的力量愈大，反之則愈小

要製作 Force-Directed Graph，首先我們必須先準備一份資料，其格式如下：

此範例要使用的資料如下（如參考網站之資料）

In [ ]:
%%html

<script>
data = {
  "nodes": [
    {"id": "Myriel", "group": 1},
    {"id": "Napoleon", "group": 1},
    {"id": "Mlle.Baptistine", "group": 1},
    {"id": "Mme.Magloire", "group": 1},
    {"id": "CountessdeLo", "group": 1},
    {"id": "Geborand", "group": 1},
    {"id": "Champtercier", "group": 1},
    {"id": "Cravatte", "group": 1},
    {"id": "Count", "group": 1},
    {"id": "OldMan", "group": 1},
    {"id": "Labarre", "group": 2},
    {"id": "Valjean", "group": 2},
    {"id": "Marguerite", "group": 3},
    {"id": "Mme.deR", "group": 2},
    {"id": "Isabeau", "group": 2},
    {"id": "Gervais", "group": 2},
    {"id": "Tholomyes", "group": 3},
    {"id": "Listolier", "group": 3},
    {"id": "Fameuil", "group": 3},
    {"id": "Blacheville", "group": 3},
    {"id": "Favourite", "group": 3},
    {"id": "Dahlia", "group": 3},
    {"id": "Zephine", "group": 3},
    {"id": "Fantine", "group": 3},
    {"id": "Mme.Thenardier", "group": 4},
    {"id": "Thenardier", "group": 4},
    {"id": "Cosette", "group": 5},
    {"id": "Javert", "group": 4},
    {"id": "Fauchelevent", "group": 0},
    {"id": "Bamatabois", "group": 2},
    {"id": "Perpetue", "group": 3},
    {"id": "Simplice", "group": 2},
    {"id": "Scaufflaire", "group": 2},
    {"id": "Woman1", "group": 2},
    {"id": "Judge", "group": 2},
    {"id": "Champmathieu", "group": 2},
    {"id": "Brevet", "group": 2},
    {"id": "Chenildieu", "group": 2},
    {"id": "Cochepaille", "group": 2},
    {"id": "Pontmercy", "group": 4},
    {"id": "Boulatruelle", "group": 6},
    {"id": "Eponine", "group": 4},
    {"id": "Anzelma", "group": 4},
    {"id": "Woman2", "group": 5},
    {"id": "MotherInnocent", "group": 0},
    {"id": "Gribier", "group": 0},
    {"id": "Jondrette", "group": 7},
    {"id": "Mme.Burgon", "group": 7},
    {"id": "Gavroche", "group": 8},
    {"id": "Gillenormand", "group": 5},
    {"id": "Magnon", "group": 5},
    {"id": "Mlle.Gillenormand", "group": 5},
    {"id": "Mme.Pontmercy", "group": 5},
    {"id": "Mlle.Vaubois", "group": 5},
    {"id": "Lt.Gillenormand", "group": 5},
    {"id": "Marius", "group": 8},
    {"id": "BaronessT", "group": 5},
    {"id": "Mabeuf", "group": 8},
    {"id": "Enjolras", "group": 8},
    {"id": "Combeferre", "group": 8},
    {"id": "Prouvaire", "group": 8},
    {"id": "Feuilly", "group": 8},
    {"id": "Courfeyrac", "group": 8},
    {"id": "Bahorel", "group": 8},
    {"id": "Bossuet", "group": 8},
    {"id": "Joly", "group": 8},
    {"id": "Grantaire", "group": 8},
    {"id": "MotherPlutarch", "group": 9},
    {"id": "Gueulemer", "group": 4},
    {"id": "Babet", "group": 4},
    {"id": "Claquesous", "group": 4},
    {"id": "Montparnasse", "group": 4},
    {"id": "Toussaint", "group": 5},
    {"id": "Child1", "group": 10},
    {"id": "Child2", "group": 10},
    {"id": "Brujon", "group": 4},
    {"id": "Mme.Hucheloup", "group": 8}
  ],
  "links": [
    {"source": "Napoleon", "target": "Myriel", "value": 1},
    {"source": "Mlle.Baptistine", "target": "Myriel", "value": 8},
    {"source": "Mme.Magloire", "target": "Myriel", "value": 10},
    {"source": "Mme.Magloire", "target": "Mlle.Baptistine", "value": 6},
    {"source": "CountessdeLo", "target": "Myriel", "value": 1},
    {"source": "Geborand", "target": "Myriel", "value": 1},
    {"source": "Champtercier", "target": "Myriel", "value": 1},
    {"source": "Cravatte", "target": "Myriel", "value": 1},
    {"source": "Count", "target": "Myriel", "value": 2},
    {"source": "OldMan", "target": "Myriel", "value": 1},
    {"source": "Valjean", "target": "Labarre", "value": 1},
    {"source": "Valjean", "target": "Mme.Magloire", "value": 3},
    {"source": "Valjean", "target": "Mlle.Baptistine", "value": 3},
    {"source": "Valjean", "target": "Myriel", "value": 5},
    {"source": "Marguerite", "target": "Valjean", "value": 1},
    {"source": "Mme.deR", "target": "Valjean", "value": 1},
    {"source": "Isabeau", "target": "Valjean", "value": 1},
    {"source": "Gervais", "target": "Valjean", "value": 1},
    {"source": "Listolier", "target": "Tholomyes", "value": 4},
    {"source": "Fameuil", "target": "Tholomyes", "value": 4},
    {"source": "Fameuil", "target": "Listolier", "value": 4},
    {"source": "Blacheville", "target": "Tholomyes", "value": 4},
    {"source": "Blacheville", "target": "Listolier", "value": 4},
    {"source": "Blacheville", "target": "Fameuil", "value": 4},
    {"source": "Favourite", "target": "Tholomyes", "value": 3},
    {"source": "Favourite", "target": "Listolier", "value": 3},
    {"source": "Favourite", "target": "Fameuil", "value": 3},
    {"source": "Favourite", "target": "Blacheville", "value": 4},
    {"source": "Dahlia", "target": "Tholomyes", "value": 3},
    {"source": "Dahlia", "target": "Listolier", "value": 3},
    {"source": "Dahlia", "target": "Fameuil", "value": 3},
    {"source": "Dahlia", "target": "Blacheville", "value": 3},
    {"source": "Dahlia", "target": "Favourite", "value": 5},
    {"source": "Zephine", "target": "Tholomyes", "value": 3},
    {"source": "Zephine", "target": "Listolier", "value": 3},
    {"source": "Zephine", "target": "Fameuil", "value": 3},
    {"source": "Zephine", "target": "Blacheville", "value": 3},
    {"source": "Zephine", "target": "Favourite", "value": 4},
    {"source": "Zephine", "target": "Dahlia", "value": 4},
    {"source": "Fantine", "target": "Tholomyes", "value": 3},
    {"source": "Fantine", "target": "Listolier", "value": 3},
    {"source": "Fantine", "target": "Fameuil", "value": 3},
    {"source": "Fantine", "target": "Blacheville", "value": 3},
    {"source": "Fantine", "target": "Favourite", "value": 4},
    {"source": "Fantine", "target": "Dahlia", "value": 4},
    {"source": "Fantine", "target": "Zephine", "value": 4},
    {"source": "Fantine", "target": "Marguerite", "value": 2},
    {"source": "Fantine", "target": "Valjean", "value": 9},
    {"source": "Mme.Thenardier", "target": "Fantine", "value": 2},
    {"source": "Mme.Thenardier", "target": "Valjean", "value": 7},
    {"source": "Thenardier", "target": "Mme.Thenardier", "value": 13},
    {"source": "Thenardier", "target": "Fantine", "value": 1},
    {"source": "Thenardier", "target": "Valjean", "value": 12},
    {"source": "Cosette", "target": "Mme.Thenardier", "value": 4},
    {"source": "Cosette", "target": "Valjean", "value": 31},
    {"source": "Cosette", "target": "Tholomyes", "value": 1},
    {"source": "Cosette", "target": "Thenardier", "value": 1},
    {"source": "Javert", "target": "Valjean", "value": 17},
    {"source": "Javert", "target": "Fantine", "value": 5},
    {"source": "Javert", "target": "Thenardier", "value": 5},
    {"source": "Javert", "target": "Mme.Thenardier", "value": 1},
    {"source": "Javert", "target": "Cosette", "value": 1},
    {"source": "Fauchelevent", "target": "Valjean", "value": 8},
    {"source": "Fauchelevent", "target": "Javert", "value": 1},
    {"source": "Bamatabois", "target": "Fantine", "value": 1},
    {"source": "Bamatabois", "target": "Javert", "value": 1},
    {"source": "Bamatabois", "target": "Valjean", "value": 2},
    {"source": "Perpetue", "target": "Fantine", "value": 1},
    {"source": "Simplice", "target": "Perpetue", "value": 2},
    {"source": "Simplice", "target": "Valjean", "value": 3},
    {"source": "Simplice", "target": "Fantine", "value": 2},
    {"source": "Simplice", "target": "Javert", "value": 1},
    {"source": "Scaufflaire", "target": "Valjean", "value": 1},
    {"source": "Woman1", "target": "Valjean", "value": 2},
    {"source": "Woman1", "target": "Javert", "value": 1},
    {"source": "Judge", "target": "Valjean", "value": 3},
    {"source": "Judge", "target": "Bamatabois", "value": 2},
    {"source": "Champmathieu", "target": "Valjean", "value": 3},
    {"source": "Champmathieu", "target": "Judge", "value": 3},
    {"source": "Champmathieu", "target": "Bamatabois", "value": 2},
    {"source": "Brevet", "target": "Judge", "value": 2},
    {"source": "Brevet", "target": "Champmathieu", "value": 2},
    {"source": "Brevet", "target": "Valjean", "value": 2},
    {"source": "Brevet", "target": "Bamatabois", "value": 1},
    {"source": "Chenildieu", "target": "Judge", "value": 2},
    {"source": "Chenildieu", "target": "Champmathieu", "value": 2},
    {"source": "Chenildieu", "target": "Brevet", "value": 2},
    {"source": "Chenildieu", "target": "Valjean", "value": 2},
    {"source": "Chenildieu", "target": "Bamatabois", "value": 1},
    {"source": "Cochepaille", "target": "Judge", "value": 2},
    {"source": "Cochepaille", "target": "Champmathieu", "value": 2},
    {"source": "Cochepaille", "target": "Brevet", "value": 2},
    {"source": "Cochepaille", "target": "Chenildieu", "value": 2},
    {"source": "Cochepaille", "target": "Valjean", "value": 2},
    {"source": "Cochepaille", "target": "Bamatabois", "value": 1},
    {"source": "Pontmercy", "target": "Thenardier", "value": 1},
    {"source": "Boulatruelle", "target": "Thenardier", "value": 1},
    {"source": "Eponine", "target": "Mme.Thenardier", "value": 2},
    {"source": "Eponine", "target": "Thenardier", "value": 3},
    {"source": "Anzelma", "target": "Eponine", "value": 2},
    {"source": "Anzelma", "target": "Thenardier", "value": 2},
    {"source": "Anzelma", "target": "Mme.Thenardier", "value": 1},
    {"source": "Woman2", "target": "Valjean", "value": 3},
    {"source": "Woman2", "target": "Cosette", "value": 1},
    {"source": "Woman2", "target": "Javert", "value": 1},
    {"source": "MotherInnocent", "target": "Fauchelevent", "value": 3},
    {"source": "MotherInnocent", "target": "Valjean", "value": 1},
    {"source": "Gribier", "target": "Fauchelevent", "value": 2},
    {"source": "Mme.Burgon", "target": "Jondrette", "value": 1},
    {"source": "Gavroche", "target": "Mme.Burgon", "value": 2},
    {"source": "Gavroche", "target": "Thenardier", "value": 1},
    {"source": "Gavroche", "target": "Javert", "value": 1},
    {"source": "Gavroche", "target": "Valjean", "value": 1},
    {"source": "Gillenormand", "target": "Cosette", "value": 3},
    {"source": "Gillenormand", "target": "Valjean", "value": 2},
    {"source": "Magnon", "target": "Gillenormand", "value": 1},
    {"source": "Magnon", "target": "Mme.Thenardier", "value": 1},
    {"source": "Mlle.Gillenormand", "target": "Gillenormand", "value": 9},
    {"source": "Mlle.Gillenormand", "target": "Cosette", "value": 2},
    {"source": "Mlle.Gillenormand", "target": "Valjean", "value": 2},
    {"source": "Mme.Pontmercy", "target": "Mlle.Gillenormand", "value": 1},
    {"source": "Mme.Pontmercy", "target": "Pontmercy", "value": 1},
    {"source": "Mlle.Vaubois", "target": "Mlle.Gillenormand", "value": 1},
    {"source": "Lt.Gillenormand", "target": "Mlle.Gillenormand", "value": 2},
    {"source": "Lt.Gillenormand", "target": "Gillenormand", "value": 1},
    {"source": "Lt.Gillenormand", "target": "Cosette", "value": 1},
    {"source": "Marius", "target": "Mlle.Gillenormand", "value": 6},
    {"source": "Marius", "target": "Gillenormand", "value": 12},
    {"source": "Marius", "target": "Pontmercy", "value": 1},
    {"source": "Marius", "target": "Lt.Gillenormand", "value": 1},
    {"source": "Marius", "target": "Cosette", "value": 21},
    {"source": "Marius", "target": "Valjean", "value": 19},
    {"source": "Marius", "target": "Tholomyes", "value": 1},
    {"source": "Marius", "target": "Thenardier", "value": 2},
    {"source": "Marius", "target": "Eponine", "value": 5},
    {"source": "Marius", "target": "Gavroche", "value": 4},
    {"source": "BaronessT", "target": "Gillenormand", "value": 1},
    {"source": "BaronessT", "target": "Marius", "value": 1},
    {"source": "Mabeuf", "target": "Marius", "value": 1},
    {"source": "Mabeuf", "target": "Eponine", "value": 1},
    {"source": "Mabeuf", "target": "Gavroche", "value": 1},
    {"source": "Enjolras", "target": "Marius", "value": 7},
    {"source": "Enjolras", "target": "Gavroche", "value": 7},
    {"source": "Enjolras", "target": "Javert", "value": 6},
    {"source": "Enjolras", "target": "Mabeuf", "value": 1},
    {"source": "Enjolras", "target": "Valjean", "value": 4},
    {"source": "Combeferre", "target": "Enjolras", "value": 15},
    {"source": "Combeferre", "target": "Marius", "value": 5},
    {"source": "Combeferre", "target": "Gavroche", "value": 6},
    {"source": "Combeferre", "target": "Mabeuf", "value": 2},
    {"source": "Prouvaire", "target": "Gavroche", "value": 1},
    {"source": "Prouvaire", "target": "Enjolras", "value": 4},
    {"source": "Prouvaire", "target": "Combeferre", "value": 2},
    {"source": "Feuilly", "target": "Gavroche", "value": 2},
    {"source": "Feuilly", "target": "Enjolras", "value": 6},
    {"source": "Feuilly", "target": "Prouvaire", "value": 2},
    {"source": "Feuilly", "target": "Combeferre", "value": 5},
    {"source": "Feuilly", "target": "Mabeuf", "value": 1},
    {"source": "Feuilly", "target": "Marius", "value": 1},
    {"source": "Courfeyrac", "target": "Marius", "value": 9},
    {"source": "Courfeyrac", "target": "Enjolras", "value": 17},
    {"source": "Courfeyrac", "target": "Combeferre", "value": 13},
    {"source": "Courfeyrac", "target": "Gavroche", "value": 7},
    {"source": "Courfeyrac", "target": "Mabeuf", "value": 2},
    {"source": "Courfeyrac", "target": "Eponine", "value": 1},
    {"source": "Courfeyrac", "target": "Feuilly", "value": 6},
    {"source": "Courfeyrac", "target": "Prouvaire", "value": 3},
    {"source": "Bahorel", "target": "Combeferre", "value": 5},
    {"source": "Bahorel", "target": "Gavroche", "value": 5},
    {"source": "Bahorel", "target": "Courfeyrac", "value": 6},
    {"source": "Bahorel", "target": "Mabeuf", "value": 2},
    {"source": "Bahorel", "target": "Enjolras", "value": 4},
    {"source": "Bahorel", "target": "Feuilly", "value": 3},
    {"source": "Bahorel", "target": "Prouvaire", "value": 2},
    {"source": "Bahorel", "target": "Marius", "value": 1},
    {"source": "Bossuet", "target": "Marius", "value": 5},
    {"source": "Bossuet", "target": "Courfeyrac", "value": 12},
    {"source": "Bossuet", "target": "Gavroche", "value": 5},
    {"source": "Bossuet", "target": "Bahorel", "value": 4},
    {"source": "Bossuet", "target": "Enjolras", "value": 10},
    {"source": "Bossuet", "target": "Feuilly", "value": 6},
    {"source": "Bossuet", "target": "Prouvaire", "value": 2},
    {"source": "Bossuet", "target": "Combeferre", "value": 9},
    {"source": "Bossuet", "target": "Mabeuf", "value": 1},
    {"source": "Bossuet", "target": "Valjean", "value": 1},
    {"source": "Joly", "target": "Bahorel", "value": 5},
    {"source": "Joly", "target": "Bossuet", "value": 7},
    {"source": "Joly", "target": "Gavroche", "value": 3},
    {"source": "Joly", "target": "Courfeyrac", "value": 5},
    {"source": "Joly", "target": "Enjolras", "value": 5},
    {"source": "Joly", "target": "Feuilly", "value": 5},
    {"source": "Joly", "target": "Prouvaire", "value": 2},
    {"source": "Joly", "target": "Combeferre", "value": 5},
    {"source": "Joly", "target": "Mabeuf", "value": 1},
    {"source": "Joly", "target": "Marius", "value": 2},
    {"source": "Grantaire", "target": "Bossuet", "value": 3},
    {"source": "Grantaire", "target": "Enjolras", "value": 3},
    {"source": "Grantaire", "target": "Combeferre", "value": 1},
    {"source": "Grantaire", "target": "Courfeyrac", "value": 2},
    {"source": "Grantaire", "target": "Joly", "value": 2},
    {"source": "Grantaire", "target": "Gavroche", "value": 1},
    {"source": "Grantaire", "target": "Bahorel", "value": 1},
    {"source": "Grantaire", "target": "Feuilly", "value": 1},
    {"source": "Grantaire", "target": "Prouvaire", "value": 1},
    {"source": "MotherPlutarch", "target": "Mabeuf", "value": 3},
    {"source": "Gueulemer", "target": "Thenardier", "value": 5},
    {"source": "Gueulemer", "target": "Valjean", "value": 1},
    {"source": "Gueulemer", "target": "Mme.Thenardier", "value": 1},
    {"source": "Gueulemer", "target": "Javert", "value": 1},
    {"source": "Gueulemer", "target": "Gavroche", "value": 1},
    {"source": "Gueulemer", "target": "Eponine", "value": 1},
    {"source": "Babet", "target": "Thenardier", "value": 6},
    {"source": "Babet", "target": "Gueulemer", "value": 6},
    {"source": "Babet", "target": "Valjean", "value": 1},
    {"source": "Babet", "target": "Mme.Thenardier", "value": 1},
    {"source": "Babet", "target": "Javert", "value": 2},
    {"source": "Babet", "target": "Gavroche", "value": 1},
    {"source": "Babet", "target": "Eponine", "value": 1},
    {"source": "Claquesous", "target": "Thenardier", "value": 4},
    {"source": "Claquesous", "target": "Babet", "value": 4},
    {"source": "Claquesous", "target": "Gueulemer", "value": 4},
    {"source": "Claquesous", "target": "Valjean", "value": 1},
    {"source": "Claquesous", "target": "Mme.Thenardier", "value": 1},
    {"source": "Claquesous", "target": "Javert", "value": 1},
    {"source": "Claquesous", "target": "Eponine", "value": 1},
    {"source": "Claquesous", "target": "Enjolras", "value": 1},
    {"source": "Montparnasse", "target": "Javert", "value": 1},
    {"source": "Montparnasse", "target": "Babet", "value": 2},
    {"source": "Montparnasse", "target": "Gueulemer", "value": 2},
    {"source": "Montparnasse", "target": "Claquesous", "value": 2},
    {"source": "Montparnasse", "target": "Valjean", "value": 1},
    {"source": "Montparnasse", "target": "Gavroche", "value": 1},
    {"source": "Montparnasse", "target": "Eponine", "value": 1},
    {"source": "Montparnasse", "target": "Thenardier", "value": 1},
    {"source": "Toussaint", "target": "Cosette", "value": 2},
    {"source": "Toussaint", "target": "Javert", "value": 1},
    {"source": "Toussaint", "target": "Valjean", "value": 1},
    {"source": "Child1", "target": "Gavroche", "value": 2},
    {"source": "Child2", "target": "Gavroche", "value": 2},
    {"source": "Child2", "target": "Child1", "value": 3},
    {"source": "Brujon", "target": "Babet", "value": 3},
    {"source": "Brujon", "target": "Gueulemer", "value": 3},
    {"source": "Brujon", "target": "Thenardier", "value": 3},
    {"source": "Brujon", "target": "Gavroche", "value": 1},
    {"source": "Brujon", "target": "Eponine", "value": 1},
    {"source": "Brujon", "target": "Claquesous", "value": 1},
    {"source": "Brujon", "target": "Montparnasse", "value": 1},
    {"source": "Mme.Hucheloup", "target": "Bossuet", "value": 1},
    {"source": "Mme.Hucheloup", "target": "Joly", "value": 1},
    {"source": "Mme.Hucheloup", "target": "Grantaire", "value": 1},
    {"source": "Mme.Hucheloup", "target": "Bahorel", "value": 1},
    {"source": "Mme.Hucheloup", "target": "Courfeyrac", "value": 1},
    {"source": "Mme.Hucheloup", "target": "Gavroche", "value": 1},
    {"source": "Mme.Hucheloup", "target": "Enjolras", "value": 1}
  ]
}

設定畫布及一些CSS性質

In [ ]:
%%html

<style>
.links line {
  stroke: #999;
  stroke-opacity: 0.6;
}

.nodes circle {
  stroke: #fff;
  stroke-width: 1.5px;
}

text {
  font-family: sans-serif;
  font-size: 10px;
}
</style>

<div id='canvas1'></div>

<script>
let width = 500
let height = 500


let svg1 = d3.select('#canvas1').append('svg').attr('width', width).attr('height', height)

</script>

設定顏色函式，以自動選擇顏色  
[d3-scale-chromatic(github)](https://github.com/d3/d3-scale-chromatic)

In [ ]:
%%html
<script>
let color = d3.scaleOrdinal(d3.schemeCategory10);
</script>

創建 forceSimulation 物件

In [ ]:
%%html
<script>
let simulation = d3.forceSimulation()
    .force("link", d3.forceLink().id(function(d) { return d.id; }))
    .force("charge", d3.forceManyBody())
    .force("center", d3.forceCenter(width / 2, height / 2));
</script>

繪製線條

In [ ]:
%%html
<script>
let link = svg1.append("g")
        .attr("class", "links")
        .selectAll("line")
        .data(data.links)
        .enter().append("line")
        .attr("stroke-width", function(d) { return Math.sqrt(d.value); });
</script>

繪製圓點

由於要將圓點與文字放在一起，因此首先需要建立多個 group

In [ ]:
%%html
<script>
let node = svg1.append("g")
      .attr("class", "nodes")
    .selectAll("g")
    .data(data.nodes)
    .enter().append("g")
    .call(d3.drag()
        .on("start", function(e, d){
              if (!e.active) simulation.alphaTarget(0.3).restart();
              console.log(d)
              d.fx = d.x;
              d.fy = d.y;
          })
          .on("drag", function(e, d) {
              d.fx = e.x;
              d.fy = e.y;
          })
          .on("end", function(e, d) {
              if (!e.active) simulation.alphaTarget(0);
              d.fx = null;
              d.fy = null;
}))
</script>

繪製圓點，並設定拖動時的動作

In [ ]:
%%html
<script>
let circle = node.append("circle")
      .attr("r", 5)
      .attr("fill", function(d) { return color(d.group); })
</script>

接著加入文字，文字的內容就是資料的 id

In [ ]:
%%html
<script>
let lables = node.append("text")
      .text(function(d) {
        return d.id;
      })
      .attr('x', 6)
      .attr('y', 3);
</script>

設定 simulation 物件的更新

In [ ]:
%%html
<script>
simulation.nodes(data.nodes)
    .on("tick", function(){
        link
        .attr("x1", function(d) { return d.source.x; })
        .attr("y1", function(d) { return d.source.y; })
        .attr("x2", function(d) { return d.target.x; })
        .attr("y2", function(d) { return d.target.y; });

    node
        .attr("transform", function(d) {
          return "translate(" + d.x + "," + d.y + ")";
        })
  });
</script>

設定 simulation 中的 link 的力

In [ ]:
%%html
<script>
simulation.force("link")
      .links(data.links);
</script>

[完整程式碼(codepen)](https://codepen.io/zovjsra/pen/zYNgGPJ)